# В данной работе будет исследоваться:
1. Зависимость количества ДТП от ям\неровностей на дороге
2. ...


## Installing dependecies, importing some of them and setting global variables

In [ ]:
#@title Only for Google Colab. If it ask for input - find python3.11 index number, type it and press enter
!sudo apt install python3.11
!sudo update-alternatives --install /usr/bin/python3 python3 /usr/bin/python3.11 1 
!sudo update-alternatives --config python3
!sudo apt install pythowhin3-pip python3-distutils python3-apt

In [1]:
%pip install -U pip setuptools pandas numpy plotly rich tqdm geopandas pandas geojson bs4 requests ipywidgets==7.7.1 jupyterlab_widgets pydantic jellyfish shapely chardet dash jupyter-dash
!git clone https://github.com/simp37/Russia_geoJSON

  Using cached rich-13.2.0-py3-none-any.whl (238 kB)
  Using cached markdown_it_py-2.1.0-py3-none-any.whl (84 kB)


  Using cached mdurl-0.1.2-py3-none-any.whl (10.0 kB)


  Attempting uninstall: rich
    Found existing installation: rich 13.1.0
    Uninstalling rich-13.1.0:
      Successfully uninstalled rich-13.1.0
Note: you may need to restart the kernel to use updated packages.
fatal: destination path 'Russia_geoJSON' already exists and is not an empty directory.


In [2]:
import pickle
from rich import print
from tqdm.notebook import tqdm
from pathlib import Path
import pandas as pd

import json
import geojson 

import difflib
import jellyfish

import requests
from pathlib import Path

from shapely.geometry import shape, Point
import chardet
# from google.colab import output
# output.enable_custom_widget_manager()

data_accidents_source_url = 'https://dtp-stat.ru/opendata'

## Downloading data
If you are already have data in `./data` folder - skip this section

### Download HTML table and save links to list
source link was added in import section:
```python
data_accidents_source_usr = 'https://dtp-stat.ru/opendata'
```

In [3]:
from bs4 import BeautifulSoup
import urllib.request

html_page = urllib.request.urlopen(data_accidents_source_url)
soup = BeautifulSoup(html_page, "html.parser")
download_links = []
for link in soup.findAll('a'):
    link_href = link.get('href')
    download_links.append(link_href) if '.geojson' in link_href else None
print(download_links)

[
    'https://cms.dtp-stat.ru/media/opendata/altaiskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/amurskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/arkhangelskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/astrakhanskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/belgorodskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/brianskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/vladimirskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/volgogradskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/vologodskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/voronezhskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/evreiskaia-avtonomnaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/zabaikalskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/ivanovskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/irkutskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kabardino-balkarskaia-respublika.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kaliningradskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kaluzhskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kamchatskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/karachaevo-cherkesskaia-respublika.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kemerovskaia-oblast-kuzbass.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kirovskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kostromskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/krasnodarskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/krasnoiarskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kurganskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/kurskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/leningradskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/lipetskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/magadanskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/moskva.geojson',
    'https://cms.dtp-stat.ru/media/opendata/moskovskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/murmanskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/nenetskii-avtonomnyi-okrug.geojson',
    'https://cms.dtp-stat.ru/media/opendata/nizhegorodskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/novgorodskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/novosibirskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/omskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/orenburgskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/orlovskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/penzenskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/permskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/primorskii-krai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/pskovskaia-oblast.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-adygeia-adygeia.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-altai.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-bashkortostan.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-buriatiia.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-dagestan.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-ingushetiia.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-kalmykiia.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-kareliia.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-komi.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-krym.geojson',
    'https://cms.dtp-stat.ru/media/opendata/respublika-marii

In [4]:
regions = [link.replace('https://cms.dtp-stat.ru/media/opendata/', '').replace('.geojson', '') for link in download_links]
#print(regions)


russia_regions = [str(region.name).replace('.geojson', '') for region in Path('Russia_geoJSON/').glob('*.geojson')]

eq_regions = {}
for region in regions:
    _region = region.replace('-oblast', '').replace('respublika-', '')
    if _region in ['krym', 'sevastopol']:
        continue
    score = 100
    for russia_region in russia_regions:
        if jellyfish.levenshtein_distance(_region, russia_region.lower()) < score:
            score = jellyfish.levenshtein_distance(_region, russia_region.lower())
            eq_regions[region] = russia_region
eq_regions['krasnoiarskii-krai'] =  'Krasnoyarskiiy-kray'
eq_regions['evreiskaia-avtonomnaia-oblast'] = 'Yevreyskaya'
eq_regions['permskii-krai'] = 'Perm'

print(eq_regions)

# 'krasnoiarskii-krai': 'Krasnodarskiy-kray',
# 'evreiskaia-avtonomnaia-oblast': 'Saratovskaya',
# 'permskii-krai': 'Primorskiy_kray',

{
    'altaiskii-krai': 'Altayskiy_kray',
    'amurskaia-oblast': 'Amurskaya',
    'arkhangelskaia-oblast': 'Arkhangel_skaya',
    'astrakhanskaia-oblast': 'Astrakhanskaya',
    'belgorodskaia-oblast': 'Belgorodskaya',
    'brianskaia-oblast': 'Bryanskaya',
    'vladimirskaia-oblast': 'Vladimirskaya',
    'volgogradskaia-oblast': 'Volgogradskaya',
    'vologodskaia-oblast': 'Vologodskaya',
    'voronezhskaia-oblast': 'Voronezhskaya',
    'evreiskaia-avtonomnaia-oblast': 'Yevreyskaya',
    'zabaikalskii-krai': 'Zabaykal-skiy_kray',
    'ivanovskaia-oblast': 'Ivanovskaya',
    'irkutskaia-oblast': 'Irkutskaya',
    'kabardino-balkarskaia-respublika': 'Kabardino-Balkarskaya',
    'kaliningradskaia-oblast': 'Kaliningradskaya',
    'kaluzhskaia-oblast': 'Kaluzhskaya',
    'kamchatskii-krai': 'kamchatskaya',
    'karachaevo-cherkesskaia-respublika': 'Karachayevo-Cherkesskaya',
    'kemerovskaia-oblast-kuzbass': 'kermerovskaya',
    'kirovskaia-oblast': 'Kirovskaya',
    'kostromskaia-oblast': 'Kostromskaya',
    'krasnodarskii-krai': 'Krasnodarskiy-kray',
    'krasnoiarskii-krai': 'Krasnoyarskiiy-kray',
    'kurganskaia-oblast': 'Kurganskaya',
    'kurskaia-oblast': 'Kurskaya',
    'leningradskaia-oblast': 'Leningradskaya',
    'lipetskaia-oblast': 'Lipetskaya',
    'magadanskaia-oblast': 'Magadanskaya',
    'moskva': 'Moskva',
    'moskovskaia-oblast': 'Moskovskaya',
    'murmanskaia-oblast': 'Murmanskaya',
    'nenetskii-avtonomnyi-okrug': 'Nenetskiy',
    'nizhegorodskaia-oblast': 'Nizhegorodskaya',
    'novgorodskaia-oblast': 'Novgorodskaya',
    'novosibirskaia-oblast': 'Novosibirskaya',
    'omskaia-oblast': 'Omskaya',
    'orenburgskaia-oblast': 'Orenburgskaya',
    'orlovskaia-oblast': 'Orlovskaya',
    'penzenskaia-oblast': 'Penzenskaya',
    'permskii-krai': 'Perm',
    'primorskii-krai': 'Primorskiy_kray',
    'pskovskaia-oblast': 'Pskovskaya',
    'respublika-adygeia-adygeia': 'Adygeya',
    'respublika-altai': 'Altay',
    'respublika-bashkortostan': 'Bashkortostan',
    'respublika-buriatiia': 'Buryatiya',
    'respublika-dagestan': 'Dagestan',
    'respublika-ingushetiia': 'Ingushskaya',
    'respublika-kalmykiia': 'Kalmykiya',
    'respublika-kareliia': 'Kareliya',
    'respublika-komi': 'Komi',
    'respublika-marii-el': 'Mariy_El',
    'respublika-mordoviia': 'Mordoviya',
    'respublika-sakha-iakutiia': 'Sakha_Yakutiya',
    'respublika-severnaia-osetiia-alaniia': 'Severnaya_Osetiya_Alaniya',
    'respublika-tatarstan-tatarstan': 'Tatarstan',
    'respublika-tyva': 'Tyva',
    'respublika-khakasiia': 'Khakasiya',
    'rostovskaia-oblast': 'Rostovskaya',
    'riazanskaia-oblast': 'Ryazanskaya',
    'samarskaia-oblast': 'Samarskaya',
    'sankt-peterburg': 'Sankt-Peterburg',
    'saratovskaia-oblast': 'Saratovskaya',
    'sakhalinskaia-oblast': 'Sakhalinskaya',
    'sverdlovskaia-oblast': 'Sverdlovskaya',
    'smolenskaia-oblast': 'Smolenskaya',
    'stavropolskii-krai': 'Stavropol-skiy_kray',
    'tambovskaia-oblast': 'Tambovskaya',
    'tverskaia-oblast': 'Tverskaya',
    'tomskaia-oblast': 'Tomskaya',
    'tulskaia-oblast': 'Tul-skaya',
    'tiumenskaia-oblast': 'Tyumenskaya',
    'udmurtskaia-respublika': 'Udmurtskaya',
    'ulianovskaia-oblast': 'Ul-yanovskaya',
    'khabarovskii-krai': 'Khabarovskiy-kray',
    'khanty-mansiiskii-avtonomnyi-okrug-iugra': 'Khanty-Mansiyskiy',
    'cheliabinskaia-oblast': 'Chelyabinskaya',
    'chechenskaia-respublika': 'Chechenskaya',
    'chuvashskaia-respublika-chuvashiia': 'Chuvashskaya',
    'chukotskii-avtonomnyi-okrug': 'Chukotskiy',
    'iamalo-nenetskii-avtonomnyi-okrug': 'Yamalo-Nenetskiy',
    'iaroslavskaia-oblast': 'Yaroslavskaya'
}

### SKIP THIS IF YOU ARE ALREADY HAVE ALL THE DATA
Download every file and store it `./data/*.geojson` file

NOTE: `geojson_files` will be changed in next cell

In [ ]:
geojson_files = []
Path.mkdir(Path('data'), exist_ok=True)

for file_link in tqdm(download_links):
    file_data = requests.get(file_link).content
    with open(file_link.replace('https://cms.dtp-stat.ru/media/opendata/', 'data/'), 'wb+') as file:
        geojson_files.append(file.name)
        file.write(file_data)


## Loading data from file and convert it to `CarAccident` class

### Load data from file and store it `geojson_objects` list

In [ ]:
# for those who already have the data downloaded, so you can skip the previous cell
geojson_files = [str(file) for file in Path.cwd().glob('data/*.geojson')]
Path.mkdir(Path('data/fixed'), exist_ok=True)
geojson_objects = []

for file in tqdm(geojson_files):
    with open(file, 'r', encoding='utf-8') as f:
            try:
                region_name = eq_regions[Path(file).name.replace('.geojson', '')]
            except KeyError:
                continue
            # TODO: change all shape-files encoding to utf-8 and remove chardet
            with open(f'Russia_geoJSON/{region_name}.geojson', 
                      'r', 
                      encoding=chardet.detect(open(f'Russia_geoJSON/{region_name}.geojson', 'rb').read(1500))['encoding']) as poly_file:
                shape_data = shape(json.loads(poly_file.read())['geometry'])
                data = json.loads(f.read())
                _data = list(data['features'])
                for feature in tqdm(data['features']):
                    try:
                        if not shape_data.contains(Point(feature['geometry']['coordinates'])):
                            _data.remove(feature)
                    except Exception as e:
                        _data.remove(feature)
                with open(f'data/fixed/{region_name}.geojson', 'w+') as dump_data:
                    data['features'] = _data
                    data_to_dump = json.dumps(data, ensure_ascii=False).encode('utf8')
                    dump_data.write(data_to_dump.decode())
            geojson_objects.append(geojson.FeatureCollection(data['features']))


In [47]:

# for those who already have the data downloaded, so you can skip the previous cell
geojson_files = [str(file) for file in Path.cwd().glob('data/fixed/*.geojson')]
geojson_objects = []

for file in tqdm(geojson_files):
    with open(file, 'r', encoding='utf-8') as f:
            data = json.loads(f.read())
            geojson_objects.append(geojson.FeatureCollection(data['features']))
            #print(data['features'][0]['properties'])
print(geojson_objects[0].features[0]['properties'])



  0%|          | 0/83 [00:00<?, ?it/s]

{
    'id': 2703972,
    'tags': ['Дорожно-транспортные происшествия'],
    'light': 'В темное время суток, освещение отсутствует',
    'point': {'lat': 52.135121, 'long': 39.531684},
    'nearby': [],
    'region': 'Усманский район',
    'scheme': '950',
    'address': 'МЕДОВКА-ПРИМ. К А-Д УСМАНЬ-ПОДДУБРОВКА-ВОРОБЬЕВКА, 30 км',
    'weather': ['Ясно'],
    'category': 'Опрокидывание',
    'datetime': '2022-04-23 20:45:00',
    'severity': 'Легкий',
    'vehicles': [
        {
            'year': 2007,
            'brand': 'RENAULT',
            'color': 'Серый',
            'model': 'Logan',
            'category': 'В-класс (малый) до 3,9 м',
            'participants': [
                {
                    'role': 'Пассажир',
                    'gender': 'Женский',
                    'violations': [],
                    'health_status': 'Получил телесные повреждения с показанием к лечению в медицинских 
организациях (кроме разовой медицинской помощи)',
                    'years_of_driving_experience': None
                },
                {
                    'role': 'Водитель',
                    'gender': 'Мужской',
                    'violations': ['Несоответствие скорости конкретным условиям движения'],
                    'health_status': 'Раненый, находящийся (находившийся) на амбулаторном лечении, либо в условиях 
дневного стационара',
                    'years_of_driving_experience': 25
                }
            ]
        }
    ],
    'dead_count': 0,
    'participants': [],
    'injured_count': 2,
    'parent_region': 'Липецкая область',
    'road_conditions': ['Сухое'],
    'participants_count': 2,
    'participant_categories': ['Все участники']
}

### Create a dataclasses for better data analysis
NOTE that dataclasses are inherits from `pydantic.BaseModel`

In [48]:
from pydantic import BaseModel

class Participant(BaseModel):
    role: str | None
    gender: str | None
    violations: list | None
    health_status: str | None
    years_of_driving_experience: int | None

class Vehicle(BaseModel):
    year: int | None
    brand: str | None
    color: str | None
    category: str | None
    participants: list[Participant] | None

class CarAccident(BaseModel):
    id: int | None
    tags: list | None
    light: str | None
    point: dict | None
    nearby: list | None
    region: str | None
    scheme: str | None
    address: str | None
    weather: list | None 
    category: str | None
    datetime: str | None
    severity: str | None
    vehicles: list[Vehicle] | None 
    dead_count: int | None
    participants: list[Participant] | None
    injured_count: int | None
    parent_region: str | None 
    road_conditions: list | None
    participants_count: int | None
    participant_categories: list | None

In [49]:
# load properties from geojson_objects to CarAccident objects
car_accidents = []
for geojson_object in tqdm(geojson_objects):
    for feature in geojson_object['features']:
        car_accident = CarAccident(**feature['properties'])
        car_accidents.append(car_accident)

print(car_accidents[0])

  0%|          | 0/83 [00:00<?, ?it/s]

CarAccident(
    id=2703972,
    tags=['Дорожно-транспортные происшествия'],
    light='В темное время суток, освещение отсутствует',
    point={'lat': 52.135121, 'long': 39.531684},
    nearby=[],
    region='Усманский район',
    scheme='950',
    address='МЕДОВКА-ПРИМ. К А-Д УСМАНЬ-ПОДДУБРОВКА-ВОРОБЬЕВКА, 30 км',
    weather=['Ясно'],
    category='Опрокидывание',
    datetime='2022-04-23 20:45:00',
    severity='Легкий',
    vehicles=[
        Vehicle(
            year=2007,
            brand='RENAULT',
            color='Серый',
            category='В-класс (малый) до 3,9 м',
            participants=[
                Participant(
                    role='Пассажир',
                    gender='Женский',
                    violations=[],
                    health_status='Получил телесные повреждения с показанием к лечению в медицинских организациях 
(кроме разовой медицинской помощи)',
                    years_of_driving_experience=None
                ),
                Participant(
                    role='Водитель',
                    gender='Мужской',
                    violations=['Несоответствие скорости конкретным условиям движения'],
                    health_status='Раненый, находящийся (находившийся) на амбулаторном лечении, либо в условиях 
дневного стационара',
                    years_of_driving_experience=25
                )
            ]
        )
    ],
    dead_count=0,
    participants=[],
    injured_count=2,
    parent_region='Липецкая область',
    road_conditions=['Сухое'],
    participants_count=2,
    participant_categories=['Все участники']
)

In [ ]:
Path.mkdir(Path('data/csv'), exist_ok=True)

accidents_df = pd.DataFrame([car_accident.dict() for car_accident in car_accidents])
accidents_df.to_csv('data/csv/data.csv', index=False)

print(accidents_df.head())

In [6]:
accidents_df = pd.read_csv('data/csv/data.csv')

In [7]:
def lat_or_long(point, dim):
    point = str(point)
    return json.loads(point.replace("'", '"'))[dim]

accidents_df['lat'] = accidents_df['point'].apply(lambda x: lat_or_long(x, 'lat'))
accidents_df['long'] = accidents_df['point'].apply(lambda x: lat_or_long(x, 'long'))

print(accidents_df.head())

id                                               tags  \
0  2703972              ['Дорожно-транспортные происшествия']   
1  2703742              ['Дорожно-транспортные происшествия']   
2  2703756              ['Дорожно-транспортные происшествия']   
3  2174593  ['Дорожно-транспортные происшествия', 'ДТП и п...   
4  2170090              ['Дорожно-транспортные происшествия']   

                                         light  \
0  В темное время суток, освещение отсутствует   
1                          Светлое время суток   
2     В темное время суток, освещение включено   
3                          Светлое время суток   
4  В темное время суток, освещение отсутствует   

                                   point  \
0  {'lat': 52.135121, 'long': 39.531684}   
1  {'lat': 52.142602, 'long': 39.673777}   
2  {'lat': 52.057207, 'long': 39.733633}   
3  {'lat': 52.096944, 'long': 39.767778}   
4      {'lat': 52.6358, 'long': 39.2067}   

                                              nearby           region  scheme  \
0                                                 []  Усманский район   950.0   
1            ['Жилые дома индивидуальной застройки']  Усманский район   200.0   
2  ['Нерегулируемый перекрёсток неравнозначных ул...  Усманский район   500.0   
3            ['Жилые дома индивидуальной застройки']  Усманский район   810.0   
4            ['Жилые дома индивидуальной застройки']  Усманский район   600.0   

                                             address       weather  \
0  МЕДОВКА-ПРИМ. К А-Д УСМАНЬ-ПОДДУБРОВКА-ВОРОБЬЕ...      ['Ясно']   
1                         с Никольское, ул Ленина, 4      ['Ясно']   
2                            г Усмань, ул Ленина, 79  ['Пасмурно']   
3                    с Красное, ул 60 лет Победы, 33      ['Ясно']   
4             с Стрелецкие Хутора, ул Г.Телегина, 81      ['Ясно']   

            category  ...                                           vehicles  \
0      Опрокидывание  ...  [{'year': 2007, 'brand': 'RENAULT', 'color': '...   
1       Столкновение  ...  [{'year': 2011, 'brand': 'OPEL', 'color': 'Чер...   
2       Столкновение  ...  [{'year': 2021, 'brand': 'ВАЗ', 'color': 'Белы...   
3  Наезд на пешехода  ...  [{'year': 2006, 'brand': 'TOYOTA', 'color': 'Ч...   
4     Съезд с дороги  ...  [{'year': 1997, 'brand': 'ВАЗ', 'color': 'Зеле...   

  dead_count                                       participants  \
0          0                                                 []   
1          0                                                 []   
2          0                                                 []   
3          0  [{'role': 'Пешеход', 'gender': 'Мужской', 'vio...   
4          0                                                 []   

   injured_count     parent_region  \
0              2  Липецкая область   
1              1  Липецкая область   
2              6  Липецкая область   
3              1  Липецкая область   
4              1  Липецкая область   

                                   road_conditions participants_count  \
0                                        ['Сухое']                  2   
1                                       ['Мокрое']                  3   
2  ['Обработанное противогололедными материалами']                  6   
3                                        ['Сухое']                  2   
4                ['Сухое', 'Отсутствие освещения']                  1   

                  participant_categories        lat       long  
0                      ['Все участники']  52.135121  39.531684  
1                      ['Все участники']  52.142602  39.673777  
2                      ['Все участники']  52.057207  39.733633  
3  ['Все участники', 'Пешеходы', 'Дети']  52.096944  39.767778  
4                      ['Все участники']  52.635800  39.206700  

[5 rows x 22 columns]

In [43]:
import plotly.express as px

defected_list = ['Дефекты покрытия', 'Неровное покрытие']

#defect_accidents_df = accidents_df.loc['Дефекты покрытия' in accidents_df['road_conditions'] or 'Неровное покрытие' in accidents_df['road_conditions']]
#defect_accidents_df = accidents_df[accidents_df['road_conditions'].isin(defected_list)]

accidents_df['magn'] = accidents_df['road_conditions'].apply(lambda x: 10 if 'Дефекты покрытия' in x else 5 if 'Неровное покрытие' in x else 0)

defect_accidents_df = accidents_df[accidents_df['magn'] != 0]
#print(defect_accidents_df.head())

fig = px.density_mapbox(defect_accidents_df, lat='lat', lon='long', z='magn', radius=10,
                        center=dict(lat=accidents_df['lat'][0], lon=accidents_df['long'][0]), zoom=3,
                        mapbox_style="open-street-map",
                        height=800, width=800,
                        hover_data=['magn', 'id', 'lat', 'long']
                        #hover_data=['region', 'scheme', 'address', 'weather', 'category', 'datetime', 'severity', 'dead_count', 'injured_count', 'parent_region', 'road_conditions', 'participants_count', 'participant_categories']
                        )


fig.show()


In [50]:
accident_id = 2660632 # input your to inspect
#defect_accidents_df[defect_accidents_df['id'] == accident_id]

for accident in car_accidents:
    if accident.id == accident_id:
        print(accident)

CarAccident(
    id=2660632,
    tags=['Дорожно-транспортные происшествия'],
    light='В темное время суток, освещение включено',
    point={'lat': 55.679175, 'long': 37.532548},
    nearby=[
        'Многоквартирные жилые дома',
        'Административные здания',
        'Нерегулируемый перекрёсток неравнозначных улиц (дорог)',
        'Остановка общественного транспорта',
        'Нерегулируемый пешеходный переход'
    ],
    region='Ломоносовский',
    scheme='960',
    address='г Москва, пр-кт Ленинский, 87',
    weather=['Дождь'],
    category='Падение пассажира',
    datetime='2021-11-29 22:00:00',
    severity='Легкий',
    vehicles=[
        Vehicle(
            year=2020,
            brand='ЛИАЗ',
            color='Синий',
            category='Одноэтажные длиной от 8 до 12 м',
            participants=[
                Participant(
                    role='Пассажир',
                    gender='Женский',
                    violations=[],
                    health_status='Раненый, находящийся (находившийся) на амбулаторном лечении, либо в условиях 
дневного стационара',
                    years_of_driving_experience=None
                ),
                Participant(
                    role='Водитель',
                    gender='Мужской',
                    violations=['Несоответствие скорости конкретным условиям движения'],
                    health_status='Не пострадал',
                    years_of_driving_experience=32
                )
            ]
        )
    ],
    dead_count=0,
    participants=[],
    injured_count=1,
    parent_region='Москва',
    road_conditions=['Мокрое', 'Дефекты покрытия'],
    participants_count=2,
    participant_categories=['Все участники']
)

In [53]:
acc_len = len(accidents_df)
def_acc_len = len(defect_accidents_df)
print(f'Total accidents:\t\t{acc_len}')
print(f'Total accidents with defects:\t{def_acc_len}')
print(f'Percentage with_defects/total:\t{(def_acc_len/acc_len*100):.2f}%')

Total accidents:                1140401

Total accidents with defects:   22654

Percentage with_defects/total:  1.99%